**Nonlinear least squares method.** Assume that we have a function $\mathbf{F} \colon U \subseteq \mathbb{R}^n \to \mathbb{R}^m$ where $m>n$, and we would like to solve the system $$\mathbf{F}(\mathbf{x}) = \mathbf{0} \textrm{. }$$

Since the number of equations is greater than the number of unknowns, such a system in general admits no solution. As in the case of linear systems we ask ourselves: What would be the best approximation to a solution? A good choice (as in the case of linear systems) is to find some $\mathbf{x} \in U$ which minimises $\|\mathbf{F}(\mathbf{x})\|^2$. An efficient way to find a solution of a nonlinear least-squares problem is the _Gauss-Newton_ iteration, of 
which one step can be written as $$\mathbf{x}^{(k+1)} = \mathbf{x}^{(k)} - \big(J_\mathbf{F}(\mathbf{x}^{(k)})\big)^{+} \mathbf{F}(\mathbf{x}^{(k)}) \textrm{. }$$

(Unlike Newton's method, where we find the solution $\mathbf{z}$ to the linear system $(J_\mathbf{F}(\mathbf{x}^{(k)}))\mathbf{z} = \mathbf{F}(\mathbf{x}^{(k)})$, we now find the solution to the _linear least-squares problem_. The term $(J_\mathbf{F})^{+}$ above is just a compact way of remembering the actual iteration step. The method only works well for overdetermined systems with full rank for which there is no need to actually evaluate the Moore-Penrose pseudo-inverse.) More precisely, the Gauss-Newton iteration will (with a little luck) produce a local minimum of the function $\mathbf{x} \mapsto \|\mathbf{F}(\mathbf{x})\|^2$. 

**Task 1** 
Find the parameters $a$ and $b$, such that the function $$f(x) = \frac{a x}{b + x}$$ best fits the data in the table below.

| $x_i$ | 0.038 | 0.194 | 0.425 | 0.626 | 1.253 | 2.500 | 3.740 |
|:-----:|:-----:|:-----:|:-----:|:-----:|:-----:|:-----:|:-----:|
| $y_i$ | **0.050** | **0.127** | **0.094** | **0.2122** | **0.2729** | **0.2665** | **0.3317** |

(This data is already entered below for convenience.)

- Find the solution using Newton's method - find the zero of the derivative of the function $\mathbf{x} \mapsto \|\mathbf{F}(\mathbf{x})\|^2$.
- Find the solution using the Gauss-Newton method.

In [ ]:
# data from the table above
xi = [0.038; 0.194; 0.425; 0.626; 1.253; 2.5; 3.74]
yi = [0.05; 0.127; 0.094; 0.2122; 0.2729; 0.2665; 0.3317]

# we include the file with the `newton` function
include("labs5.jl")
# define F and JF
F(X) = ### YOUR CODE HERE ###
JF(X) = ### YOUR CODE HERE ###
# let's now find the minimum of F'*F 
# the gradient of F'*F and its Jacobian matrix
G(X) = ### YOUR CODE HERE ###
JG(X) = ### YOUR CODE HERE ###
newton(G, JG, [0.5; 0.5]).X

In [ ]:
# call to perform the Gauss-Newton method with original F, we simply call `newton`
a, b = newton(F, JF, [0.5; 0.5]).X

In [ ]:
# let's plot the data points and the 'best fit' we found
using Plots
### YOUR CODE HERE ###

**Task 2**
Let's improve the solution to the task from the 2nd week of lab sessions: We have $n$ known transmitter positions $(p_1,q_1), \ldots , (p_n, q_n)$ in $\mathbb{R}^2$. We need to determine the location of a receiver knowning the distances $d_1, \ldots, d_n$ form the transmitters. Ideally (with exact measurements) we need to find the solution to the system of equations $$(x-p_i)^2 + (y-q_i)^2 = d_i^2 \textrm{ where } i = 1, \ldots, n \textrm{. }$$

Improve the function `X = receiver([pi, qi], [di])` from the second week using the Gauss-Newton method. The solution to the linear least squares problem we found can serve as the initial guess $\mathbf{x}^{(0)}$.

In [ ]:
function receiver(transmitters, distances)
    # get the size of the data
    n = length(transmitters)
    # reserve memory for A and b
    A = zeros(n-1, 2)
    b = zeros(n-1, 1)
    # intialize the values ...
    pj1, qj1 = transmitters[1]
    dj1 = distances[1]
    # ... for the for loop
    for j = 2:n
        pj, qj = transmitters[j]
        dj = distances[j]
        A[j-1, :] = 2*[pj-pj1 qj-qj1]
        b[j-1] = (pj^2 - pj1^2) + (qj^2 - qj1^2) - (dj^2 - dj1^2)
        # set *_j1 for the next iteration
        pj1, qj1 = pj, qj
        dj1 = dj
    end
    
    # nonlinear improvement to A\b
    ### YOUR CODE HERE ###

    return Tuple(newton(F, JF, A\b).X)
end

In [ ]:
tx = [(0, 1), (1, 1), (1, 0), (-1, -1)]
dist = [1, 1.4, 1, 1.4]
receiver(tx, dist)

**Finding a local minimum of a multivariate function**
Our second interest today will be finding a (local) minimum of a multivariate function $f \colon U \to \mathbf{R}$, where $U \subseteq \mathbb{R}^n$. (Of course, we already know how to do that with appropriate use of Newton's iteration.) The _gradient descent method_ (tries to) find a minimum of a function $f \colon U \to \mathbb{R}$ by starting with some initial guess $\mathbf{x}^{(0)}$, and then continue iteratively:
\begin{align*}
	\mathbf{x}^{(1)} &= \mathbf{x}^{(0)} - \alpha \mathop{grad} f (\mathbf{x}^{(0)}) \textrm{, } \\
	\mathbf{x}^{(2)} &= \mathbf{x}^{(1)} - \alpha \mathop{grad} f (\mathbf{x}^{(1)}) \textrm{, } \\
			    &\ \; \vdots \\
	\mathbf{x}^{(k+1)} &= \mathbf{x}^{(k)} - \alpha \mathop{grad} f (\mathbf{x}^{(k)}) \textrm{. }
\end{align*}
Here, the step size $\alpha > 0$ is a carefully chosen (small) real number. (The convergence of such method depends on $f$, initial guess $\mathbf{x}^{(0)}$, and the choice of $\alpha$.) 

**Task 3** A function $f$ is given by $$f(x,y) = (1-x)^2 + 4(y-x^2)^2 \textrm{. }$$

- Find the minimum of $f$.
- Find (an approximation for) the minimum of the function $f$ using the gradient descent method. Write a _Julia_ function `gradmet(gradf, alpha, x0, tol, maxit)`, which runs this method for the function `f` with gradient `gradf`, step size `alpha`, and initial guess `x0`. (We use `maxit` to limit the maximum allowed number of iterations, and `tol` to prescribe desired accuracy.)

In [ ]:
function gradmet(gradf, alpha, x0; tol = 1e-6, maxit = 10000)
    n = 1
    x = x0
    ### YOUR CODE HERE ###

    # a warning if maxit was reached
    if n == maxit
        @warn "no convergence after $maxit iterations"
    end
    # let's return a named tuple
    return (X = x, n = n)
end

In [ ]:
gradf(X) = ### YOUR CODE HERE ###
gradmet(gradf, 0.01, [1; 0]; tol = 1e-16)

In [ ]:
# we can also use the gradient method to solve task 1 (with G = grad(F'*F))
gradmet(G, 0.2, [0.5; 0.5]).X